https://www.bcn.cat/estadistica/castella/dades/inf/lecpadro/lec17/t12.htm

In [8]:
import warnings
warnings.filterwarnings("ignore")

In [9]:
import numpy as np
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
import pandas as pd
import matplotlib.pyplot as plt
pd.set_option('display.max_columns',None)

from requirements import *
import pandas as pd
import seaborn as sns
from matplotlib import pyplot
from collections import Counter
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import scipy.cluster.hierarchy as sch
from sklearn.preprocessing import normalize
from sklearn import preprocessing
import geopandas as gpd
import folium
from folium import plugins
from datetime import timedelta, date
import shapely
from shapely.geometry import Polygon, Point
from matplotlib import dates as dt
from shapely.wkt import loads
import networkx as nx
from heapq import nsmallest
pd.set_option('display.max_columns', None)
sns.set(font_scale=1)

De moment, per fer un test població general de Barcelona:

# Funcions 

In [10]:
filename = 'data/income/generated_geodataISC.geojson'
data_coords = gpd.read_file(filename)
data_coords['centroids'] = data_coords['geometry'].centroid

In [11]:
def get_N_closest_ABS(N,ABS): 
    distances = []
    distances = [get_distance_ABS(ABS,data.CODIABS) for i,data in barcelona.iterrows() ]
    sort = sorted(distances, key=lambda x: x[1])[:N]
    ids = [i[0] for i in sort]
    return ids

In [12]:
def get_distance_ABS(source,target):
    p1 = [data_coords[data_coords.CODIABS == source].centroids.x.values,data_coords[data_coords.CODIABS == target].centroids.y.values]
    p2 = [data_coords[data_coords.CODIABS == target].centroids.x.values,data_coords[data_coords.CODIABS == target].centroids.y.values]
    #print(p1,p2)
    return np.sqrt(((p1[0]-p2[0])**2)+((p1[1]-p2[1])**2))[0]

In [13]:
def random_points_within(poly, num_points):
    min_x, min_y, max_x, max_y = poly.bounds

    points = []
    lon = []
    lat = []
    while len(points) < num_points:
        random_point = Point([random.uniform(min_x, max_x), random.uniform(min_y, max_y)])
        if (random_point.within(poly)):
            points.append(random_point)
            lon.append(random_point.x)
            lat.append(random_point.y)

    return pd.Series(lon),pd.Series(lat)

In [14]:
##creates the list with [Lat,Lon,Heat] for every day
def heat_generation(data):
    max_value = data.NumCasos.max()
    alpha = 1000
    heat_list = [
        [
            [
                row.Latitud,
                row.Longitud,
                alpha*np.log(1 + row.NumCasos / max_value)
                / (1 + alpha * np.log(1 + row.NumCasos / max_value)),
            ]
            #
            for index, row in data[data.TipusCasData == i].iterrows()
        ]
        #for each day
        for i in data.TipusCasData.unique()
    ]
    return heat_list

In [15]:
##plot the timelapse
def plot(heat_list,location,zoom,rati,data):
    mapa = folium.Map(location = location,#[41.723864,1.901103],
                         zoom_start=zoom,#7.5,
                         ratio = rati,# 40,
                         tiles = "cartodbpositron")

    heatmap = plugins.HeatMapWithTime(
        heat_list,
        index=list(data.TipusCasData.unique()),
        name="Timelapse",
        auto_play=True,
        max_opacity=0.2
    )
    heatmap.add_to(mapa)
    # Layercontrols lets you change visuals in the html page
    ctrl = folium.LayerControl()
    ctrl.add_to(mapa)
    return mapa

In [16]:
def generate_datapoints_inside_area(location,nodes,colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred', 'darkblue', 'darkgreen', 'cadetblue', 'darkpurple', 'pink', 'lightblue', 'lightgreen', 'black']):
#per cada ABS, generarem tants punts dins de la ubicació com població té 
    frames = []
    nodes = nodes.reset_index()
    for ABS in nodes.CODIABS.unique():
        #get points inside the area
        cens_abs = nodes[nodes['CODIABS']==ABS]
        cens_abs = cens_abs.reset_index()
        ## generem n punts dins la ABS
        poly = location.loc[ABS]['geometry']
        lon,lat = random_points_within(poly,len(cens_abs))
        
        #print(lon,lat)
        #we will assign different points inside the polygon area
        '''subdf = pd.DataFrame()
        subdf['Longitud'] = lon.values
        subdf['Latitud'] = lat.values   
        subdf = subdf.to_dict(orient = 'list')'''
        cens_abs['Longitud'] = lon
        cens_abs['Latitud'] = lat
        cens_abs['color'] = random.choice(colors)
        #print(cens_abs)
        frames.append(cens_abs)
        #cens_abs.drop(cens_abs.index, inplace=True)
        
    return pd.concat(frames)


In [17]:
def plotDot(row):
    dot = folium.CircleMarker(location=[row.Latitud, row.Longitud],
                        radius=2,
                        weight=3.5,color = row.color,opacity=0.6)
    dot.add_to(this_map)
    
def get_neigh_points(node):
    targets = network[network.id1 == node]['id2']
    neighs = []
    try:
        for t in targets:
            p = barcelona_generated_dataframe[barcelona_generated_dataframe.id1 == t].to_dict('records')[0]
            #get coords 
            coords = [p['Latitud'],p['Longitud']]
            neighs.append(coords)
    except:
        pass
    return neighs
    
def plotLine(row):
    #get source coords
    nodeSource = row.id1
    source_coords = [row.Latitud,row.Longitud]
    neighbors = get_neigh_points(nodeSource)
    #print(neighbors)
    for n in neighbors:
        t = [tuple(source_coords),tuple(n)]
        
        try:
            folium.PolyLine(t, color="lightgrey", weight=1, opacity=0.3).add_to(this_map)
        except:
            print(n)

# Importem dades espacials

In [18]:
filename = 'data/income/generated_geodataISC.geojson'
data = gpd.read_file(filename)
data.head()

CODIABS    ABSDescrip  NumCasos        ISC  POBLACIÓ      ratio   Income  \
0      379      LLEIDA 7      2045  28.885710     17381  11.765721      NaN   
1      138      LLEIDA 4      2890  51.264958     27056  10.681549      NaN   
2      248    TERRASSA B      2553  70.236305     27907   9.148242  20835.0   
3      345  SABADELL 4-B      2101  53.888378     24233   8.669995  21603.0   
4      191   SABADELL 1B      1716  34.717657     21175   8.103896  22625.0   

                                            geometry  
0  POLYGON ((0.51817 41.64841, 0.51831 41.64851, ...  
1  POLYGON ((0.61470 41.66671, 0.61479 41.66677, ...  
2  POLYGON ((2.04803 41.58482, 2.04878 41.58497, ...  
3  POLYGON ((2.08925 41.54729, 2.08915 41.54732, ...  
4  POLYGON ((2.12643 41.53260, 2.12455 41.53348, ...

In [19]:
data = data.to_crs(epsg=4326)
data['centroids'] = data['geometry'].centroid

Filtrem per la zona de Barcelona.

In [20]:
barcelona = data[data.ABSDescrip.str.contains('BARCELONA')]

# Importem la xarxa

In [21]:
colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred', 'darkblue', 'darkgreen', 'cadetblue', 'darkpurple', 'pink', 'lightblue', 'lightgreen', 'black']

In [23]:
nodes = pd.read_excel('data/nodes_Barcelona.xlsx')
nodes.drop(columns=['Unnamed: 0'],inplace=True)
nodes.head()

id1  Edat  Ocupacio  Educacio  Genere  PNumContactes
0  1577     0         3         1       0             17
1  1578     0         3         1       0             17
2  1583     2         3         1       0             17
3  1600     3         6         2       0             16
4  1620     3         6         2       0             16

## Assignar a cada ABS N individus

In [24]:
data['POBLACIÓ'] = data['POBLACIÓ'].floordiv(1000)

In [25]:
## assignem els ABS
barcelona = data[data.ABSDescrip.str.contains('BARCELONA')]
network_assign = nodes.copy()
frames = []

for index, d in barcelona.iterrows():
    
    samp = network_assign.sample(n = d['POBLACIÓ'])
    
    network_assign.drop(labels = samp.index,axis = 0,inplace=True)
    samp['CODIABS'] = d.CODIABS
    frames.append(samp)
nodes = pd.concat(frames)#.reset_index()
nodes.head()

id1  Edat  Ocupacio  Educacio  Genere  PNumContactes  CODIABS
679    399     2         3         1       0              2      383
1384  1310     3         6         2       0              2      383
60    1530     3         6         3       1              8      383
782   1183     1         6         3       0              2      383
1450   121     0         3         1       0              1      383

In [26]:
barcelona = barcelona.set_index(['CODIABS'])


In [27]:
barcelona_generated_dataframe = generate_datapoints_inside_area(barcelona,nodes)
barcelona_generated_dataframe = barcelona_generated_dataframe.dropna()

In [28]:
barcelona_generated_dataframe.drop(columns = 'level_0',inplace=True)
barcelona_generated_dataframe.drop(columns = 'index',inplace=True)
barcelona_generated_dataframe.head()

id1  Edat  Ocupacio  Educacio  Genere  PNumContactes  CODIABS  Longitud  \
0   399     2         3         1       0              2      383  2.138546   
1  1310     3         6         2       0              2      383  2.139810   
2  1530     3         6         3       1              8      383  2.139745   
3  1183     1         6         3       0              2      383  2.140459   
4   121     0         3         1       0              1      383  2.140670   

     Latitud color  
0  41.364037   red  
1  41.367048   red  
2  41.364385   red  
3  41.365570   red  
4  41.361939   red

### Matriu distancies ABS

In [7]:
'''
%%time

matrix = pd.DataFrame(columns = barcelona.index)
for ab1 in barcelona.index:
    for ab2 in barcelona.index:
        matrix.loc[ab1,ab2] = get_distance_ABS(ab1,ab2)
matrix.to_excel('matrix_distances.xlsx')'''

"\n%%time\n\nmatrix = pd.DataFrame(columns = barcelona.index)\nfor ab1 in barcelona.index:\n    for ab2 in barcelona.index:\n        matrix.loc[ab1,ab2] = get_distance_ABS(ab1,ab2)\nmatrix.to_excel('matrix_distances.xlsx')"

In [30]:
matrix = pd.read_excel('matrix_distances.xlsx')
matrix.drop(columns=['Unnamed: 0'],inplace=True)
matrix = matrix.set_index(matrix.columns)
matrix.head()

383       32        70        79        71        18        19   \
383  0.000000  0.030579  0.053295  0.064830  0.055340  0.037707  0.032883   
32   0.030579  0.000000  0.022716  0.034251  0.024761  0.007128  0.002304   
70   0.053295  0.022716  0.000000  0.011534  0.002044  0.015588  0.020413   
79   0.064830  0.034251  0.011534  0.000000  0.009490  0.027123  0.031947   
71   0.055340  0.024761  0.002044  0.009490  0.000000  0.017633  0.022457   

          33        35        17        28        20        21        24   \
383  0.012062  0.000750  0.043500  0.039273  0.027733  0.018926  0.022282   
32   0.018517  0.031329  0.012921  0.008694  0.002846  0.011653  0.008297   
70   0.041233  0.054045  0.009796  0.014023  0.025562  0.034370  0.031013   
79   0.052767  0.065579  0.021330  0.025557  0.037096  0.045904  0.042548   
71   0.043277  0.056089  0.011840  0.016067  0.027606  0.036414  0.033057   

          22        38        23        25        39        27        42   \
383  0.011286  0.001127  0.007171  0.015082  0.001721  0.027019  0.006004   
32   0.019293  0.031706  0.023407  0.015497  0.032300  0.003560  0.024575   
70   0.042009  0.054423  0.046124  0.038213  0.055016  0.026276  0.047291   
79   0.053543  0.065957  0.057658  0.049748  0.066551  0.037811  0.058826   
71   0.044053  0.056467  0.048168  0.040257  0.057061  0.028321  0.049336   

          48        47        30        29        31        75        76   \
383  0.018251  0.025799  0.035786  0.039976  0.034679  0.045037  0.041734   
32   0.012328  0.004780  0.005207  0.009397  0.004100  0.014458  0.011155   
70   0.035044  0.027496  0.017510  0.013319  0.018616  0.008258  0.011561   
79   0.046578  0.039031  0.029044  0.024854  0.030151  0.019793  0.023096   
71   0.037088  0.029541  0.019554  0.015364  0.020661  0.010303  0.013606   

          52        326       400       40        44        43        49   \
383  0.029185  0.035611  0.011909  0.008747  0.011876  0.001000  0.012920   
32   0.001394  0.005032  0.042488  0.039326  0.042455  0.029579  0.017659   
70   0.024111  0.017685  0.065204  0.062043  0.065172  0.052295  0.040376   
79   0.035645  0.029219  0.076738  0.073577  0.076706  0.063829  0.051910   
71   0.026155  0.019729  0.067248  0.064087  0.067216  0.054339  0.042420   

          46        50        358       53        51        54        62   \
383  0.008720  0.002442  0.016782  0.017491  0.025636  0.022507  0.028103   
32   0.039299  0.028137  0.013797  0.013088  0.004943  0.008072  0.002476   
70   0.062015  0.050854  0.036513  0.035805  0.027659  0.030788  0.025193   
79   0.073549  0.062388  0.048048  0.047339  0.039194  0.042323  0.036727   
71   0.064059  0.052898  0.038558  0.037849  0.029704  0.032833  0.027237   

          56        385       67        395       327       65        78   \
383  0.017629  0.037404  0.042962  0.049553  0.045105  0.051061  0.058416   
32   0.012950  0.006825  0.012383  0.018974  0.014526  0.020482  0.027838   
70   0.035666  0.015892  0.010333  0.003742  0.008190  0.002234  0.005121   
79   0.047201  0.027426  0.021868  0.015277  0.019724  0.013769  0.006413   
71   0.037711  0.017936  0.012378  0.005787  0.010234  0.004279  0.003077   

          77        73        331       36        16        72        74   \
383  0.050963  0.063418  0.061355  0.004093  0.049483  0.071771  0.076557   
32   0.020384  0.032839  0.030777  0.034672  0.018904  0.041192  0.045978   
70   0.002332  0.010122  0.008060  0.057388  0.003813  0.018476  0.023262   
79   0.013867  0.001412  0.003474  0.068923  0.015347  0.006941  0.011728   
71   0.004377  0.008078  0.006016  0.059433  0.005857  0.016431  0.021218   

          59        402       403       41        55        45        34   \
383  0.028813  0.039314  0.039089  0.027052  0.000665  0.046004  0.001395   
32   0.001766  0.008735  0.008510  0.057631  0.029914  0.076583  0.029184   
70   0.024482  0.013982  0.014207  0.080347  0.052631  0.099299  0.051900  

## Assignem els links: 

- 5 contactes: mateix barri
- 10 contactes: barri i barri més proper
- Més de 10 contactes: barris més llunyans

In [34]:
%%time
network = pd.DataFrame()
for index,data in barcelona_generated_dataframe.iterrows():
    abs_source = int(data.CODIABS)
    #dels contactes, eliminem el propi node
    samp = barcelona_generated_dataframe.drop(index)
    ##si tenen menys de 5 contactes: mateix "barri"
    ## si tenen entre 5-10 contactes, dos barris més propers
    ## més de 10, aleatòris
    if data.PNumContactes < 5:
        closest_n = list(matrix[abs_source].nsmallest(n=1).index)
        frames = []
        for n in range(data.PNumContactes):
            a = random.sample(closest_n,k=1)
            abs_neigh = samp[samp.CODIABS == a[0]]
            try:
                neigh = random.sample(list(abs_neigh.id1),k=1)
                frames.append(neigh[0])
            except:
                pass
    elif data.PNumContactes < 10:
        closest_n = list(matrix[abs_source].nsmallest(n=3).index)
        frames = []
        for n in range(data.PNumContactes):            
            a = random.sample(closest_n,k=1)
            abs_neigh = samp[samp.CODIABS == a[0]]
            try:
                neigh = random.sample(list(abs_neigh.id1),k=1)
                frames.append(neigh[0])
            except:
                pass
    else:
        closest_n = list(matrix[abs_source].index)
        frames = []
        for n in range(data.PNumContactes):
            a = random.sample(closest_n,k=1)
            abs_neigh = samp[samp.CODIABS == a[0]]
            try:
                neigh = random.sample(list(abs_neigh.id1),k=1)
                frames.append(neigh[0])
            except:
                pass

    #sub_dataframe = pd.concat(frames)
    #cons = sub_dataframe.sample(n=int(data.PNumContactes)).id1.values
    for i in frames:
        data['id2'] = i
        network = network.append(data) 

CPU times: user 2min 13s, sys: 0 ns, total: 2min 13s
Wall time: 4min 27s


In [36]:
 #network = network.astype(int)
network = network.drop_duplicates(subset = ['id1','id2'])
network

CODIABS  Edat  Educacio  Genere    Latitud  Longitud  Ocupacio  \
0     383.0   2.0       1.0     0.0  41.364037  2.138546       3.0   
0     383.0   2.0       1.0     0.0  41.364037  2.138546       3.0   
1     383.0   3.0       2.0     0.0  41.367048  2.139810       6.0   
1     383.0   3.0       2.0     0.0  41.367048  2.139810       6.0   
2     383.0   3.0       3.0     1.0  41.364385  2.139745       6.0   
..      ...   ...       ...     ...        ...       ...       ...   
22    396.0   2.0       3.0     1.0  41.445999  2.192593       6.0   
22    396.0   2.0       3.0     1.0  41.445999  2.192593       6.0   
23    396.0   2.0       3.0     0.0  41.442437  2.191528       6.0   
23    396.0   2.0       3.0     0.0  41.442437  2.191528       6.0   
23    396.0   2.0       3.0     0.0  41.442437  2.191528       6.0   

    PNumContactes      color     id1     id2  
0             2.0        red   399.0   791.0  
0             2.0        red   399.0   232.0  
1             2.0        red  1310.0  1198.0  
1             2.0        red  1310.0    44.0  
2             8.0        red  1530.0   811.0  
..            ...        ...     ...     ...  
22            3.0  cadetblue   625.0  1289.0  
22            3.0  cadetblue   625.0  1458.0  
23            3.0  cadetblue   648.0  1469.0  
23            3.0  cadetblue   648.0   400.0  
23            3.0  cadetblue   648.0   833.0  

[4939 rows x 11 columns]

In [42]:
network.to_excel('data/network_edat_closest_n_v2.xlsx')

### Generem la xarxa

In [37]:
cnetwork = nx.from_pandas_edgelist(network,'id1','id2', create_using=nx.MultiGraph)

for ind,data in network.iterrows():
        cnetwork.add_node(data.id1 ,edat = data.Edat)

In [38]:
len(cnetwork.edges)

4939

In [39]:
len(cnetwork.nodes)

1610

In [40]:
this_map = folium.Map(location = [41.723864,1.901103],
                         zoom_start=10,
                         ratio =40,
                         tiles = "cartodbpositron")

#use df.apply(,axis=1) to "iterate" through every row in your dataframe
barcelona_generated_dataframe.apply(plotLine, axis = 1)
barcelona_generated_dataframe.apply(plotDot, axis = 1)

#Set the zoom to the maximum possible
this_map.fit_bounds(this_map.get_bounds())

#Save the map to an HTML file
this_map.save('map.html')

this_map